# ---------------------------------------------------------------------
# File Name: building_extension.py
# Purpose: CityGML building objects are randomly choosen and extended in given height  
# Author: Nico Ehlers
# Created: 2024-07-08
# ---------------------------------------------------------------------

In [ ]:
import pandas as pd
import os
import ipywidgets as widgets
from IPython.display import display
from choose_extrusion_buildings import choose_building
from build_up_geometries import bldg_extrusion
from gml_parsing import little_parser

In [ ]:
# Create input widgets
residential_code_input = widgets.Text(description='Residential Code:', value='31001_1000')# '31001_1010' Asberg)
bldg_extension_input = widgets.IntSlider(description='Building Extension:', min=0, max=5, step=1, value=2)
extrusion_percentage_input = widgets.FloatSlider(description='Extrusion Percentage:', min=0.0, max=1.0, step=0.1, value=1.0)
floor_height_input = widgets.FloatText(description='Floor Height:', value=3.5)
gml_path_input = widgets.Text(description='GML Path:', value=os.getcwd()+'\GML_files\\')
gml_file_input = widgets.Text(description='GML File:', value='Grombuehl_LoD2_mini.gml')#Grafenbühl.gml

In [ ]:
# Create button widget
run_button = widgets.Button(description='Run Code')

# Create output widget
output = widgets.Output()

In [ ]:
gml_path =os.getcwd()+'\GML_files\\'
gml_file = 'Grombuehl_LoD2_mini.gml'

save_name = gml_file.split('.')[0]+'_'
gml_info = little_parser(gml_path+gml_file)
gml_par = gml_info.little_parser()

In [ ]:
# Define function to run when button is clicked
def run_code(button):
    with output:
        # Get user inputs
        residential_code = residential_code_input.value
        bldg_extension = bldg_extension_input.value
        extrusion_percentage = extrusion_percentage_input.value
        floor_height = floor_height_input.value
        gml_path = gml_path_input.value
        gml_file = gml_file_input.value

        file_path = gml_path + gml_file
        # Run choose_building and bldg_extrusion classes
        #----------------------------------------------------------------------------
        ### GML PARSING
        #----------------------------------------------------------------------------
        save_name = gml_file.split('.')[0]+'_'
        gml_info = little_parser(file_path)
        gml_par = gml_info.little_parser()
        #----------------------------------------------------------------------------
        ### choose buildings for extrusion
        #----------------------------------------------------------------------------
        # TODO: at the moment all construction massive
        gml_par['construction_type'] = 'massive'
        extr = choose_building(gml_par, bldg_extension, residential_code, extrusion_percentage)
        gml_par = extr.choose_building()
        # filter buildings with residential code
        gml_par = gml_par[gml_par['function'] == residential_code].reset_index(drop=True)
        #----------------------------------------------------------------------------
        ### GML extrusion
        #----------------------------------------------------------------------------
        # Example usage
        output_file_path = gml_path + gml_file.replace('.gml', '_extruded.gml')

        extrude_gml = bldg_extrusion(gml_par, file_path, output_file_path, floor_height, residential_code)
        extrude_gml.bldg_extrusion()

        # Print confirmation message
        print('Code executed successfully!')

In [ ]:
# Attach function to button click event
run_button.on_click(run_code)

# Display the widgets
display(residential_code_input, bldg_extension_input, extrusion_percentage_input, floor_height_input, gml_path_input, gml_file_input, run_button, output)